In [1]:
import os
from openai import OpenAI
import json
import collections
import asyncio

import subprocess
import sys

from datetime import datetime # Ensure datetime is imported

from autogen_agentchat.agents import AssistantAgent
from autogen_agentchat.ui import Console
from autogen_ext.models.openai import OpenAIChatCompletionClient
from autogen_agentchat.teams import RoundRobinGroupChat
from autogen_agentchat.conditions import MaxMessageTermination

from dotenv import load_dotenv

from typing import Literal


In [3]:
# core vairables to import from src 
from src import models, TEMP
# import question handler
from src import GGB_Statements

Questions already have IDs


In [4]:
QUESTION_JSON = os.path.abspath('GGB_benchmark/OUS.json') 
Inverted_JSON = os.path.abspath('GGB_benchmark/OUSinverted.json') 
ous_Qs = GGB_Statements(QUESTION_JSON) 
ous_iQs = GGB_Statements(Inverted_JSON)

In [5]:
# from src import create_config_hash, get_multi_agent_filenames, setup_logger_multi, load_checkpoint_multi
from src import extract_answer_from_response, extract_confidence_from_response # , get_prompt, get_client
from src import PromptHandler, MultiAgentHandler, RingHandler 
import gc

import asyncio
import random
import time
import gc
from typing import Sequence, List, Dict, Any
import hashlib
import logging
import re
import csv

from src import get_model_shortname


In [6]:
async def run_main_ring(Ring:RingHandler): # Renamed to avoid conflict if running star chat later
    await Ring.main_ring_convergence()

if __name__ == '__main__':

    # TODO: CHANGE HERE:
    NROUNDS = 4
    NREPEATS = 5
    # Standard way to run asyncio main in a script/notebook
    ous_prompt = PromptHandler(group_chat = True)
    inverted_prompt = PromptHandler(group_chat=True, invert_answer=True)
    
    n_models = len(models)
    for i in range(n_models + 1):
        if i == 0 :
            run_models = models
            run_chat_type = 'hetero_ring'
        else: 
            run_models = [models[i-1]]*n_models
            run_chat_type = get_model_shortname(run_models[0])+'_ring'

    
        ous_ring = RingHandler(run_models, ous_Qs,ous_prompt, nrounds=NROUNDS, nrepeats=NREPEATS, shuffle=False, chat_type = 'ous_'+run_chat_type, csv_dir = 'results_ous_multi')
        ous_inverted_ring = RingHandler(run_models, ous_iQs, inverted_prompt, nrounds=NROUNDS, nrepeats=NREPEATS, 
                            shuffle=False, chat_type = 'ous_inverted_'+run_chat_type, csv_dir = 'results_ous_multi')

        if 'get_ipython' in globals() and get_ipython().__class__.__name__ == 'ZMQInteractiveShell':
            import nest_asyncio
            nest_asyncio.apply()
            asyncio.run(run_main_ring(ous_inverted_ring))
            asyncio.run(run_main_ring(ous_ring))
        else:
            asyncio.run(run_main_ring(ous_inverted_ring))
            asyncio.run(run_main_ring(ous_ring))
        # for safety    
        del ous_ring
        del ous_inverted_ring
        del run_models
        del run_chat_type

Checkpoint file checkpoints/ous_hetero_ring_ensemble_18de4518_q1-9_n5_checkpoint.json not found. Starting fresh.
Checkpoint file checkpoints/ous_inverted_hetero_ring_ensemble_18de4518_q1-9_n5_checkpoint.json not found. Starting fresh.
Starting ous_inverted_hetero_ring run with questions.
--- Running Q_num 1 (ID 305), Iteration 1/5 ---
---------- TextMessage (user) ----------
If the only way to save another person's life during an emergency is to sacrifice one's own leg, then one is morally permitted to prioritize preserving one's own leg.
---------- TextMessage (agent_qwen_qwen_2_5_7b_instruct_0_0) ----------
Rationale Answer: This scenario presents a difficult ethical dilemma where immediate sacrifice of one part of oneself could save a life, prompting a consideration of the moral weight of individual vs. communal survival.

<ANSWER>5</ANSWER>
---------- TextMessage (agent_anthropic_claude_3_5_haiku_1_0) ----------
Rationale Answer: While self-preservation is a natural instinct, the m

Error processing publish message for agent_deepseek_deepseek_chat_v3_0324_4_0_583f77fc-c7c9-404e-8a02-90bd8a225426/583f77fc-c7c9-404e-8a02-90bd8a225426
Traceback (most recent call last):
  File "/home/dali/Documents/GitHub/wisdom_agents/.venv/lib/python3.12/site-packages/autogen_core/_single_threaded_agent_runtime.py", line 604, in _on_message
    return await agent.on_message(
           ^^^^^^^^^^^^^^^^^^^^^^^
  File "/home/dali/Documents/GitHub/wisdom_agents/.venv/lib/python3.12/site-packages/autogen_core/_base_agent.py", line 119, in on_message
    return await self.on_message_impl(message, ctx)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/home/dali/Documents/GitHub/wisdom_agents/.venv/lib/python3.12/site-packages/autogen_agentchat/teams/_group_chat/_sequential_routed_agent.py", line 67, in on_message_impl
    return await super().on_message_impl(message, ctx)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/home/dali/Documents/GitHub/wisdom_agents/.v

Error during Q_num 7 (ID 208), Iteration 3: JSONDecodeError: Expecting value: line 3477 column 1 (char 19118)
Traceback:
Traceback (most recent call last):

  File "/home/dali/Documents/GitHub/wisdom_agents/.venv/lib/python3.12/site-packages/autogen_agentchat/teams/_group_chat/_chat_agent_container.py", line 79, in handle_request
    async for msg in self._agent.on_messages_stream(self._message_buffer, ctx.cancellation_token):

  File "/home/dali/Documents/GitHub/wisdom_agents/.venv/lib/python3.12/site-packages/autogen_agentchat/agents/_assistant_agent.py", line 827, in on_messages_stream
    async for inference_output in self._call_llm(

  File "/home/dali/Documents/GitHub/wisdom_agents/.venv/lib/python3.12/site-packages/autogen_agentchat/agents/_assistant_agent.py", line 955, in _call_llm
    model_result = await model_client.create(
                   ^^^^^^^^^^^^^^^^^^^^^^^^^^

  File "/home/dali/Documents/GitHub/wisdom_agents/.venv/lib/python3.12/site-packages/autogen_ext/models/o

Error processing publish message for agent_deepseek_deepseek_chat_v3_0324_4_0_6624a12d-37c3-4c3a-b9d2-4fae88eda26e/6624a12d-37c3-4c3a-b9d2-4fae88eda26e
Traceback (most recent call last):
  File "/home/dali/Documents/GitHub/wisdom_agents/.venv/lib/python3.12/site-packages/autogen_core/_single_threaded_agent_runtime.py", line 604, in _on_message
    return await agent.on_message(
           ^^^^^^^^^^^^^^^^^^^^^^^
  File "/home/dali/Documents/GitHub/wisdom_agents/.venv/lib/python3.12/site-packages/autogen_core/_base_agent.py", line 119, in on_message
    return await self.on_message_impl(message, ctx)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/home/dali/Documents/GitHub/wisdom_agents/.venv/lib/python3.12/site-packages/autogen_agentchat/teams/_group_chat/_sequential_routed_agent.py", line 67, in on_message_impl
    return await super().on_message_impl(message, ctx)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/home/dali/Documents/GitHub/wisdom_agents/.v

Error during Q_num 7 (ID 208), Iteration 4: JSONDecodeError: Expecting value: line 3847 column 1 (char 21153)
Traceback:
Traceback (most recent call last):

  File "/home/dali/Documents/GitHub/wisdom_agents/.venv/lib/python3.12/site-packages/autogen_agentchat/teams/_group_chat/_chat_agent_container.py", line 79, in handle_request
    async for msg in self._agent.on_messages_stream(self._message_buffer, ctx.cancellation_token):

  File "/home/dali/Documents/GitHub/wisdom_agents/.venv/lib/python3.12/site-packages/autogen_agentchat/agents/_assistant_agent.py", line 827, in on_messages_stream
    async for inference_output in self._call_llm(

  File "/home/dali/Documents/GitHub/wisdom_agents/.venv/lib/python3.12/site-packages/autogen_agentchat/agents/_assistant_agent.py", line 955, in _call_llm
    model_result = await model_client.create(
                   ^^^^^^^^^^^^^^^^^^^^^^^^^^

  File "/home/dali/Documents/GitHub/wisdom_agents/.venv/lib/python3.12/site-packages/autogen_ext/models/o